In [1]:
import json
import math
import os
import sys
from typing import Dict, Union, Callable, Tuple, Optional

import bpy
import mathutils
import numpy as np

In [2]:
list(bpy.data.objects)

[bpy.data.objects['Camera'],
 bpy.data.objects['Cube'],
 bpy.data.objects['Light']]

In [3]:
json_file_path = "/home/yizhou/Research/temp/2.txt"

In [4]:
args = json.loads(open(json_file_path).read())

In [5]:
args

{'data': [{'type': 'front3d',
   'houseLayoutFile': '/home/yizhou/Research/temp/Trescope/Trescope4Python/example/data/res/3D-FRONT-samples/scenes/310e0715-f95b-40ca-8edc-744560f57379.json',
   'shapeLocalSource': '/home/yizhou/Research/temp/Trescope/Trescope4Python/example/data/res/3D-FRONT-samples/3D-FUTURE-model',
   'shapeRemoteSource': {'objUrls': None, 'textureUrls': None},
   'view': None,
   'unit': 'm',
   'hiddenMeshes': ['Ceiling', 'SlabTop', 'ExtrusionCustomizedCeilingModel'],
   'renderType': 'color',
   'renderer': 'blender',
   'sampleCount': 128,
   'baseLightStrength': 8}],
 'layout': {'showlegend': True,
  'legend': {'orientation': 'h'},
  'yaxis': {'scaleanchor': 'x', 'scaleratio': 1},
  'margin': {'l': 60, 'r': 60, 't': 80, 'b': 60},
  'hoverlabel': {'namelength': -1},
  'scene': {'camera': {'eye': {'x': 2.0571141439246317,
     'y': 1.039072682672779,
     'z': -1.66250000190733},
    'up': {'x': 0, 'y': 1, 'z': 0},
    'center': {'x': 2.064691640650556,
     'y': 1

In [6]:
houseLayoutFile = "/home/yizhou/Research/3D_FRONT/3D-FRONT/db2b1031-0769-4d04-a2bd-4fe8651c8461.json"

In [7]:
shapeLocalSource = "/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/"

In [8]:
#houseLayoutFile = args['data'][0]['houseLayoutFile']
#shapeLocalSource = args['data'][0]['shapeLocalSource']
renderType = args['data'][0]['renderType']
sampleCount = args['data'][0]['sampleCount']
baseLightStrength = args['data'][0]['baseLightStrength']
eye = args['layout']['scene']['camera']['eye']
center = args['layout']['scene']['camera']['center']
up = args['layout']['scene']['camera']['up']
fovy = args['layout']['scene']['camera']['fovy']
near, far = args['layout']['scene']['camera']['near'], args['layout']['scene']['camera']['far']
width, height = args['width'], args['height']
outputFile = args['outputFile']

In [9]:
houseLayoutFile

'/home/yizhou/Research/3D_FRONT/3D-FRONT/db2b1031-0769-4d04-a2bd-4fe8651c8461.json'

In [10]:
with open(houseLayoutFile) as f: sceneDict = json.load(f)

In [11]:
sceneDict

{'uid': 'db2b1031-0769-4d04-a2bd-4fe8651c8461',
 'jobid': '',
 'design_version': '1587239126006_5271ab6b-3c1f-4bb2-9ed5-81c1ad947993',
 'code_version': '0.11',
 'north_vector': [0, 1, 0],
 'furniture': [{'uid': '7041/model',
   'jid': '73499a41-04ce-4a20-8d40-bcdc5749efdc',
   'aid': [],
   'title': 'curtain/curtain',
   'type': 'standard'},
  {'uid': '9609/model',
   'jid': '96b5e99d-72f8-41ad-b453-de7dfc4dbcf1',
   'aid': [],
   'title': 'outdoor furniture/outdoor furniture - floor-based',
   'type': 'standard'},
  {'uid': '7466/model0',
   'jid': '844f3e62-b2f4-4704-affb-ac10d3593213',
   'aid': [],
   'title': 'curtain/curtain',
   'type': 'standard'},
  {'uid': '8431/model0',
   'jid': 'ea076ba4-b8a2-47c6-a311-889f5dc1c680',
   'aid': [],
   'title': 'curtain/curtain',
   'type': 'standard'},
  {'uid': '8463/model',
   'jid': '23361f63-47ac-49a0-aeae-b05e01d5626a',
   'aid': [],
   'title': 'bed/crib',
   'type': 'standard',
   'size': [1.2486599731445311, 1.8818099975585938, 0.95

In [12]:
def __create_instance_table(sceneDict: Dict):
    _ = {'id': [], 'position': [], 'rotation': [], 'scale': [], 'ref': []}
    for room in sceneDict['scene']['room']:
        for child in room['children']:
            _['id'].append(child['instanceid'])
            _['position'].append(child['pos'])
            _['rotation'].append(child['rot'])
            _['scale'].append(child['scale'])
            _['ref'].append(child['ref'])
    return {key: np.array(value) for key, value in _.items()}

In [13]:
sceneDict['mesh'][0]

{'aid': [],
 'jid': '',
 'uid': '133511587239130256/0',
 'xyz': [1.1162,
  2.6,
  -1.0376,
  1.1173,
  2.2,
  -1.0376,
  1.1162,
  0.0,
  -1.0376,
  1.1173,
  2.2,
  -1.0376,
  1.1162,
  2.6,
  -1.0376,
  2.4397,
  2.6,
  -1.0376,
  1.1173,
  2.2,
  -1.0376,
  2.4397,
  2.6,
  -1.0376,
  2.3795,
  2.2,
  -1.0376,
  2.3795,
  2.2,
  -1.0376,
  2.4397,
  2.6,
  -1.0376,
  2.3795,
  0.0,
  -1.0376,
  2.3795,
  0.0,
  -1.0376,
  2.4397,
  2.6,
  -1.0376,
  2.4397,
  0.0,
  -1.0376,
  1.1173,
  0.0,
  -1.0376,
  1.1162,
  0.0,
  -1.0376,
  1.1173,
  2.2,
  -1.0376],
 'normal': [0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0],
 'uv': [0.0,
  0.0,
  0.0011,
  -0.4,
  0.0

In [14]:
sceneDict['scene']['room'][1]['children']

[{'ref': '7019A4F5-0CB3-4DA8-8168-8271FEB7D81C/410EEEF6-53AB-4F72-9212-FFB1BEE60DE3/23242',
  'pos': [0, 0, 0],
  'rot': [0, 0, 0, 1],
  'scale': [1, 1, 1],
  'instanceid': 'mesh/152'},
 {'ref': '5FA759F0-6F5A-45F9-A938-27F395E96C6E/88BDF266-0E36-4A55-8949-4C3962E5451C/23268',
  'pos': [0, 0, 0],
  'rot': [0, 0, 0, 1],
  'scale': [1, 1, 1],
  'instanceid': 'mesh/153'},
 {'ref': 'CE980278-8EC0-42E0-B2E6-FABA49DD0C2C/AB1F3D99-7D41-418A-B876-D34BFE80EB68/23284',
  'pos': [0, 0, 0],
  'rot': [0, 0, 0, 1],
  'scale': [1, 1, 1],
  'instanceid': 'mesh/154'},
 {'ref': '203327E6-5B71-4A2F-BF5C-D0FC72863996/06DFAA4D-F67C-4E4E-BC76-7449EA296877/23298',
  'pos': [0, 0, 0],
  'rot': [0, 0, 0, 1],
  'scale': [1, 1, 1],
  'instanceid': 'mesh/155'},
 {'ref': '12FC6BDC-3F90-4E5E-AC78-5D60F536E0EC/F2B6DD22-DCA8-45C2-998A-B542C703C7A0/23309',
  'pos': [0, 0, 0],
  'rot': [0, 0, 0, 1],
  'scale': [1, 1, 1],
  'instanceid': 'mesh/156'},
 {'ref': '01F414DA-AB2A-4D69-9265-79DB01A8511B/59AD3B51-0168-4871-B8A4

In [15]:
instance_table = __create_instance_table(sceneDict)

In [16]:
def __create_mesh_table(sceneDict: Dict):
    _ = {'id': [], 'material_id': [], 'type': [], 'xyz': [], 'normal': [], 'uv': [], 'face': []}
    for index, mesh in enumerate(sceneDict['mesh']):
        _['id'].append(mesh['uid'])
        _['material_id'].append(mesh['material'])
        _['type'].append(mesh['type'])
        _['xyz'].append(np.array(mesh['xyz']).reshape(-1, 3).T.tolist())
        _['normal'].append(np.array(mesh['normal']).reshape(-1, 3).T.tolist())
        _['uv'].append(np.array(mesh['uv']).reshape(-1, 2).T.tolist())
        _['face'].append(np.array(mesh['faces']).reshape(-1, 3).T.tolist())
    return {key: np.array(value) for (key, value) in _.items()}

In [17]:
mesh_table = __create_mesh_table(sceneDict)

/home/yizhou/blender-2.92.0-linux64/blender:11: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.


In [18]:
def __create_material_table(sceneDict: Dict, material_when_unavailable: Union[int, Callable] = 0xffffffff):
    def compatible_texture(_material):
        if 'texture' not in _material: return ''
        _texture = _material['texture']
        return _texture['value'] if isinstance(_texture, dict) else _texture

    def compatible_color(rgba_or_rgb_array):
        r, g, b, a = rgba_or_rgb_array if 4 == len(rgba_or_rgb_array) else [*rgba_or_rgb_array, 255]
        return a << 24 | r << 16 | g << 8 | b

    def compatible_color_mode(_material):
        if not bool(_material.get('texture')): return 'color'
        if 'colorMode' in _material: return _material['colorMode']
        if bool(_material.get('useColor')): return 'color'
        return 'texture'

    def compatible_uv_transform(_material):
        return np.array(_material['UVTransform']).reshape(3, 3) if 'UVTransform' in _material else np.eye(3)

    _ = {'id': [], 'texture': [], 'color': [], 'colorMode': [], 'UVTransform': [], }
    for _material in sceneDict['material']:
        _['id'].append(_material['uid'])
        try:
            _['texture'].append(compatible_texture(_material['texture']))
            _['color'].append(compatible_color(_material['color']))
            _['colorMode'].append(compatible_color_mode(_material))
            _['UVTransform'].append(compatible_uv_transform(_material))
        except:
            if isinstance(material_when_unavailable, int):
                _['texture'].append('')
                _['UVTransform'].append(np.eye(3))
                _['color'].append(material_when_unavailable)
                _['colorMode'].append('color')
            else:
                _m = material_when_unavailable(_material)
                _['texture'].append(compatible_texture(_m['texture']))
                _['UVTransform'].append(compatible_uv_transform(_m))
                _['color'].append(compatible_color(_m['color']))
                _['colorMode'].append(compatible_color_mode(_m))
    return {key: np.array(value) for key, value in _.items()}


In [19]:
material_table = __create_material_table(sceneDict)

In [20]:
def __create_furniture_table(sceneDict: Dict):
    _ = {'id': [], 'jid': []}
    for furniture in sceneDict['furniture']:
        _['id'].append(furniture['uid'])
        _['jid'].append(furniture['jid'])
    return {key: np.array(value) for key, value in _.items()}

In [21]:
furniture_table = __create_furniture_table(sceneDict)

In [22]:
def join(ndarray1Dict, ndarray2Dict, c1, c2, rsuffix):
    leftColumnNames = list(ndarray1Dict.keys())
    rightColumnNames = list(ndarray2Dict.keys())

    def rightName(_name):
        return _name if _name not in leftColumnNames else f'{rsuffix}{_name}'

    columnNames = leftColumnNames + [rightName(name) for name in rightColumnNames]
    dict1KeyIndex = list(ndarray1Dict.keys()).index(c1)
    result = []
    for row1 in zip(*ndarray1Dict.values()):
        indices = (ndarray2Dict[c2] == row1[dict1KeyIndex])
        row_join = [v[indices] for v in ndarray2Dict.values()]
        for row2 in zip(*row_join): result.append([*row1, *row2])
    columns = np.array(result).T.tolist()
    return {name: column for name, column in zip(columnNames, columns)}

In [23]:
mesh_material = join(mesh_table, material_table, 'material_id', 'id', 'material_')
mesh_all = join(mesh_material, instance_table, 'id', 'ref', 'instance_')
furniture_all = join(furniture_table, instance_table, 'id', 'ref', 'instance_')

/home/yizhou/blender-2.92.0-linux64/blender:15: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.


In [24]:
def setSceneOutput(output_file_path, width, height):
    scene = bpy.context.scene
    scene.render.resolution_percentage = 100
    scene.render.resolution_x = width
    scene.render.resolution_y = height
    scene.render.filepath = output_file_path

In [25]:
setSceneOutput(outputFile, width, height)

In [26]:
def setCycles(num_samples=128):
    scene = bpy.context.scene
    scene.render.image_settings.file_format = 'PNG'
    scene.render.engine = 'CYCLES'
    scene.cycles.samples = num_samples
    scene.view_layers[0].cycles.use_denoising = True

In [27]:
setCycles(sampleCount)

In [28]:
def normalizeScene():
    for obj in bpy.data.objects:
        if obj.name not in ['Camera']: obj.select_set(state=True)
    bpy.ops.object.delete()

In [29]:
normalizeScene()

Info: Deleted 2 object(s)


In [30]:
def setCamera(eye, center, up, fovyDegree, near, far):
    camera = bpy.data.objects['Camera']

    camera.data.angle = math.radians(fovyDegree)

    eye = np.array(list(eye.values()))
    center = np.array(list(center.values()))
    north = np.array(list(up.values()))
    direction = center - eye
    forward = -direction / np.linalg.norm(direction)
    right = np.cross(north, forward)
    up = np.cross(forward, right)
    rotation = np.vstack([right, up, forward]).T
    matrix = np.eye(4)
    matrix[:3, :3] = rotation
    matrix[:3, -1] = eye
    mm = mathutils.Matrix.Identity(4)
    for index, row in enumerate(matrix): mm[index] = row
    camera.matrix_world = mm

    return camera, (eye, center)

In [31]:
_, (npEye, npCenter) = setCamera(eye, center, up, fovy, near, far)

In [32]:
def import_and_initialize_furniture(furniture, obj_and_texture_fetcher):
    jid, position, rotation, scale = furniture
    x, y, z, w = rotation
    rotation = (w, x, y, z)
    obj_path, texture_path = obj_and_texture_fetcher(jid)
    print(obj_path, obj_path is None, texture_path, texture_path is None)

    if obj_path is None or texture_path is None: return

    for obj in bpy.data.objects: obj.select_set(False)

    obj_material = add_material(f'obj_material[{jid}]', use_nodes=True, make_node_tree_empty=False)
    tree, links, nodes = obj_material.node_tree, obj_material.node_tree.links, obj_material.node_tree.nodes
    bsdf = nodes["Principled BSDF"]
    set_principled_node(principled_node=bsdf)
    texImage = nodes.new('ShaderNodeTexImage')
    texImage.image = bpy.data.images.load(texture_path)
    links.new(bsdf.inputs['Base Color'], texImage.outputs['Color'])

    bpy.ops.import_scene.obj(filepath=obj_path, axis_forward='Y', axis_up='Z')
    for model in bpy.context.selected_objects:
        model.select_set(False)
        model.name = f'{jid}.{model.name}'

        scaleMatrix = mathutils.Matrix.Identity(4)
        scaleMatrix[0][0], scaleMatrix[1][1], scaleMatrix[2][2] = scale
        model.matrix_world = (
                mathutils.Matrix.Translation(mathutils.Vector(position)) @
                mathutils.Quaternion(rotation).to_matrix().to_4x4() @
                scaleMatrix)

        if model.data.materials:
            model.data.materials[0] = obj_material
        else:
            model.data.materials.append(obj_material)


In [33]:
furniture_list = list(zip(furniture_all['jid'], furniture_all['position'], furniture_all['rotation'], furniture_all['scale']))

In [34]:
furniture = furniture_list[0]

In [35]:
furniture

('23361f63-47ac-49a0-aeae-b05e01d5626a',
 array([-1.1609,  0.    , -3.0381]),
 array([0., 0., 0., 1.]),
 array([1., 1., 1.]))

In [36]:
def add_material(name: str = "Material", use_nodes: bool = False, make_node_tree_empty: bool = False):
    material = bpy.data.materials.new(name)
    material.use_nodes = use_nodes
    if use_nodes and make_node_tree_empty: clean_nodes(material.node_tree.nodes)
    return material

In [37]:
def set_principled_node(
        principled_node,
        base_color: Tuple[float, float, float, float] = (0.6, 0.6, 0.6, 1.0),
        subsurface: float = 0.0,
        subsurface_color: Tuple[float, float, float, float] = (0.8, 0.8, 0.8, 1.0),
        subsurface_radius: Tuple[float, float, float] = (1.0, 0.2, 0.1),
        metallic: float = 0.0,
        specular: float = 0.5,
        specular_tint: float = 0.0,
        roughness: float = 0.5,
        anisotropic: float = 0.0,
        anisotropic_rotation: float = 0.0,
        sheen: float = 0.0,
        sheen_tint: float = 0.5,
        clearcoat: float = 0.0,
        clearcoat_roughness: float = 0.03,
        ior: float = 1.45,
        transmission: float = 0.0,
        transmission_roughness: float = 0.0) -> None:
    principled_node.inputs['Base Color'].default_value = base_color
    principled_node.inputs['Subsurface'].default_value = subsurface
    principled_node.inputs['Subsurface Color'].default_value = subsurface_color
    principled_node.inputs['Subsurface Radius'].default_value = subsurface_radius
    principled_node.inputs['Metallic'].default_value = metallic
    principled_node.inputs['Specular'].default_value = specular
    principled_node.inputs['Specular Tint'].default_value = specular_tint
    principled_node.inputs['Roughness'].default_value = roughness
    principled_node.inputs['Anisotropic'].default_value = anisotropic
    principled_node.inputs['Anisotropic Rotation'].default_value = anisotropic_rotation
    principled_node.inputs['Sheen'].default_value = sheen
    principled_node.inputs['Sheen Tint'].default_value = sheen_tint
    principled_node.inputs['Clearcoat'].default_value = clearcoat
    principled_node.inputs['Clearcoat Roughness'].default_value = clearcoat_roughness
    principled_node.inputs['IOR'].default_value = ior
    principled_node.inputs['Transmission'].default_value = transmission
    principled_node.inputs['Transmission Roughness'].default_value = transmission_roughness

In [38]:
for furniture in zip(furniture_all['jid'], furniture_all['position'], furniture_all['rotation'], furniture_all['scale']):
    jid, position, rotation, scale = furniture
    raw_model_path = os.path.join(shapeLocalSource, jid, 'raw_model.obj')
    texture_path = os.path.join(shapeLocalSource, jid, 'texture.png')
    print(raw_model_path, os.path.exists(raw_model_path))
    print(texture_path, os.path.exists(texture_path))
    
    import_and_initialize_furniture(furniture, lambda jid: (
        os.path.join(shapeLocalSource, jid, 'raw_model.obj') if os.path.exists(
            os.path.join(shapeLocalSource, jid, 'raw_model.obj')) else None,
        os.path.join(shapeLocalSource, jid, 'texture.png') if os.path.exists(
            os.path.join(shapeLocalSource, jid, 'texture.png')) else None,
    ))

/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/23361f63-47ac-49a0-aeae-b05e01d5626a/raw_model.obj True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/23361f63-47ac-49a0-aeae-b05e01d5626a/texture.png True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/23361f63-47ac-49a0-aeae-b05e01d5626a/raw_model.obj False /home/yizhou/Research/3D_FRONT/3D-FUTURE-model/23361f63-47ac-49a0-aeae-b05e01d5626a/texture.png False
(  0.0000 sec |   0.0000 sec) Importing OBJ '/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/23361f63-47ac-49a0-aeae-b05e01d5626a/raw_model.obj'...
  (  0.0007 sec |   0.0002 sec) Parsing OBJ file...
WARNING, skipping malformatted line: #
WARNING, skipping malformatted line: #
WARNING, skipping malformatted line: #
WARNING, skipping malformatted line: #
WARNING, skipping malformatted line: #
WARNING, skipping malformatted line: #
WARNING, skipping malformatted line: #
WARNING, skipping malformatted line: #
WARNING, skipping malformatted line: #
WARNING, skipping malformatted line: #
W

    (  0.5864 sec |   0.5852 sec) Done, loading materials and images...
WARNING, currently unsupported 'tr' translucency option, skipped.
WARNING, currently unsupported 'tf' filter color option, skipped.
WARNING, currently unsupported ambient texture, skipped.
    (  0.5878 sec |   0.5866 sec) Done, building geometries (verts:61807 faces:38666 materials: 1 smoothgroups:0) ...
    (  0.8734 sec |   0.8722 sec) Done.
  (  0.8743 sec |   0.8738 sec) Finished importing: '/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/99a1b7c8-b3fe-47f4-851f-0bab93344121/raw_model.obj'
Progress: 100.00%

/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/03e769ca-8083-4bc3-bd90-f0f793b5aff8/raw_model.obj True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/03e769ca-8083-4bc3-bd90-f0f793b5aff8/texture.png True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/03e769ca-8083-4bc3-bd90-f0f793b5aff8/raw_model.obj False /home/yizhou/Research/3D_FRONT/3D-FUTURE-model/03e769ca-8083-4bc3-bd90-f0f793b5aff8/texture.png False


    (  0.2811 sec |   0.2798 sec) Done.
  (  0.2819 sec |   0.2814 sec) Finished importing: '/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/5c942af5-0b68-4ed8-85cf-40ff509b52f0/raw_model.obj'
Progress: 100.00%

/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/5c942af5-0b68-4ed8-85cf-40ff509b52f0/raw_model.obj True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/5c942af5-0b68-4ed8-85cf-40ff509b52f0/texture.png True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/5c942af5-0b68-4ed8-85cf-40ff509b52f0/raw_model.obj False /home/yizhou/Research/3D_FRONT/3D-FUTURE-model/5c942af5-0b68-4ed8-85cf-40ff509b52f0/texture.png False
(  0.0001 sec |   0.0001 sec) Importing OBJ '/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/5c942af5-0b68-4ed8-85cf-40ff509b52f0/raw_model.obj'...
  (  0.0006 sec |   0.0002 sec) Parsing OBJ file...
WARNING, skipping malformatted line: #
WARNING, skipping malformatted line: #
WARNING, skipping malformatted line: #
WARNING, skipping malformatted line: #
WARNING, skipping malfor

    (  0.1655 sec |   0.1645 sec) Done.
  (  0.1663 sec |   0.1659 sec) Finished importing: '/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/00acb313-c507-4372-addf-508755c6e98b/raw_model.obj'
Progress: 100.00%

/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/89eb27f1-dac4-45e2-93fa-4dc0f44e9793/raw_model.obj True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/89eb27f1-dac4-45e2-93fa-4dc0f44e9793/texture.png True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/89eb27f1-dac4-45e2-93fa-4dc0f44e9793/raw_model.obj False /home/yizhou/Research/3D_FRONT/3D-FUTURE-model/89eb27f1-dac4-45e2-93fa-4dc0f44e9793/texture.png False
(  0.0001 sec |   0.0001 sec) Importing OBJ '/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/89eb27f1-dac4-45e2-93fa-4dc0f44e9793/raw_model.obj'...
  (  0.0006 sec |   0.0002 sec) Parsing OBJ file...
WARNING, skipping malformatted line: #
WARNING, skipping malformatted line: #
WARNING, skipping malformatted line: #
WARNING, skipping malformatted line: #
WARNING, skipping malfor

    (  0.1148 sec |   0.1137 sec) Done.
  (  0.1157 sec |   0.1152 sec) Finished importing: '/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/42e54e32-06be-4ff7-9a9e-0b9704a63b23/raw_model.obj'
Progress: 100.00%

/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/15d9cd02-9336-412e-a078-c5c0cea63527/raw_model.obj True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/15d9cd02-9336-412e-a078-c5c0cea63527/texture.png True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/15d9cd02-9336-412e-a078-c5c0cea63527/raw_model.obj False /home/yizhou/Research/3D_FRONT/3D-FUTURE-model/15d9cd02-9336-412e-a078-c5c0cea63527/texture.png False
(  0.0000 sec |   0.0000 sec) Importing OBJ '/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/15d9cd02-9336-412e-a078-c5c0cea63527/raw_model.obj'...
  (  0.0006 sec |   0.0002 sec) Parsing OBJ file...
    (  0.0668 sec |   0.0659 sec) Done, loading materials and images...
WARNING, currently unsupported 'tr' translucency option, skipped.
WARNING, currently unsupported 'tf' filter

In [39]:
def create_mesh(id_, xyz, normal, uv, face, color):
    def int_to_color_rgba_array(_color) -> Tuple[float, float, float, float]:
        _color_array = [(_color & 0x00ff0000) >> 16, (_color & 0x0000ff00) >> 8, (_color & 0x000000ff) >> 0, (_color & 0xff000000) >> 24, ]
        return tuple(map(lambda e: e / 255, _color_array))

    mesh_name = f'mesh_{id_}'
    new_mesh: bpy.types.Mesh = bpy.data.meshes.new(mesh_name)
    scene = bpy.context.scene
    vertices = xyz.T.tolist()
    faces = face.T.tolist()
    new_mesh.from_pydata(vertices, [], faces)
    new_mesh.update()

    new_object: bpy.types.Object = bpy.data.objects.new(f'{mesh_name}_obj', new_mesh)
    scene.collection.objects.link(new_object)

    new_object.location = (0, 0, 0)
    new_object.scale = (1, 1, 1)
    new_object.rotation_euler = (0, 0, 0)

    material = add_material(f'{mesh_name}_material', use_nodes=True, make_node_tree_empty=False)
    tree, links, nodes = material.node_tree, material.node_tree.links, material.node_tree.nodes

    bsdf = nodes["Principled BSDF"]
    base_color = int_to_color_rgba_array(color)
    set_principled_node(
        principled_node=bsdf,
        base_color=base_color
    )
    if new_object.data.materials:
        new_object.data.materials[0] = material
    else:
        new_object.data.materials.append(material)

    return new_object


# Set Mesh

In [40]:
for index, mesh in enumerate(
            zip(mesh_all['id'], mesh_all['type'], mesh_all['xyz'], mesh_all['normal'], mesh_all['uv'], mesh_all['face'], mesh_all['color'])):
        id_, type_, xyz, normal, uv, face, color = mesh
        xyz = np.array(xyz.tolist()).astype(np.float)
        normal = np.array(normal.tolist()).astype(np.float)
        uv = np.array(uv.tolist()).astype(np.float)
        face = np.array(face.tolist()).astype(np.int)
        create_mesh(id_, xyz, normal, uv, face, color)

/home/yizhou/blender-2.92.0-linux64/blender:4: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
/home/yizhou/blender-2.92.0-linux64/blender:5: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
/home/yizhou/blender-2.92.0-linux64/blender:6: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `flo

In [41]:
def createLightPoint(location: Tuple[float, float, float] = (0.0, 0.0, 5.0), strength: float = 100, name: Optional[str] = None) -> bpy.types.Object:
    bpy.ops.object.light_add(type='POINT', location=location)
    light = bpy.context.object.data
    light.energy = strength
    if name is not None: bpy.context.object.name = name
    return bpy.context.object

In [42]:
npDirection = npCenter - npEye
npDirection = npDirection / np.linalg.norm(npDirection)
for i in range(1, 4): createLightPoint(location=(npEye + npDirection * .5 * i).tolist(), strength=baseLightStrength)

In [43]:
def startRender():
    bpy.ops.render.render(use_viewport=True, write_still=True)

In [44]:
startRender()

In [45]:
mesh_all['id']

['133511587239130256/0',
 '138681587239130264/0',
 '159681587239130269/0',
 '153221587239130273/0',
 '128341587239130320/0',
 '128341587239130320/1',
 '128341587239130320/150',
 '128341587239130320/150',
 '128341587239130320/270',
 '128501587239130725/0',
 '130281587239130735/0',
 '163071587239130739/0',
 '161941587239130743/0',
 '166141587239130836/0',
 '165171587239130841/0',
 '164201587239130845/0',
 '141751587239130849/0',
 '137551587239130853/0',
 '131251587239130865/0',
 '7019A4F5-0CB3-4DA8-8168-8271FEB7D81C/410EEEF6-53AB-4F72-9212-FFB1BEE60DE3/23242',
 '5FA759F0-6F5A-45F9-A938-27F395E96C6E/88BDF266-0E36-4A55-8949-4C3962E5451C/23268',
 'CE980278-8EC0-42E0-B2E6-FABA49DD0C2C/AB1F3D99-7D41-418A-B876-D34BFE80EB68/23284',
 '203327E6-5B71-4A2F-BF5C-D0FC72863996/06DFAA4D-F67C-4E4E-BC76-7449EA296877/23298',
 '131411587239130988/0',
 '138841587239130998/0',
 '139651587239131001/0',
 '136421587239131017/0',
 '136581587239131019/0',
 '137711587239131025/0',
 '12FC6BDC-3F90-4E5E-AC78-5D60F53

In [46]:
mesh_all_list = list(zip(mesh_all['id'], mesh_all['type'], mesh_all['xyz'], mesh_all['normal'], mesh_all['uv'], mesh_all['face'], mesh_all['color']))

In [47]:
furniture_list

[('23361f63-47ac-49a0-aeae-b05e01d5626a',
  array([-1.1609,  0.    , -3.0381]),
  array([0., 0., 0., 1.]),
  array([1., 1., 1.])),
 ('de279c41-9886-4948-bccc-d6bb7fc840c8',
  array([ 0.5565    ,  0.        , -3.33146667]),
  array([ 0.     , -0.70711,  0.     ,  0.70711]),
  array([1., 1., 1.])),
 ('6a1b87d1-9be4-456e-aeb5-5005614cdc6b',
  array([-3.3497241 ,  0.        , -2.73020025]),
  array([0.     , 0.70711, 0.     , 0.70711]),
  array([1., 1., 1.])),
 ('6914bc9b-d7f3-3d85-9fdf-a8e30b54ed35',
  array([-2.80850392,  0.        , -2.88219919]),
  array([ 0.     ,  0.90848,  0.     , -0.41794]),
  array([1., 1., 1.])),
 ('45ad43a4-af6a-4c5f-82d2-e5339d9c48ec',
  array([-3.7113,  0.85  , -2.7714]),
  array([ 0.     , -0.70711,  0.     ,  0.70711]),
  array([0.8849, 0.7647, 1.    ])),
 ('fac76ac7-35bd-4d75-a852-022696a140c1',
  array([ 0.9587,  0.    , -1.9358]),
  array([ 0.     , -0.70711,  0.     ,  0.70711]),
  array([-0.9756,  1.    ,  1.    ])),
 ('fac76ac7-35bd-4d75-a852-022696a1